In [1]:
import requests
from bs4 import BeautifulSoup
import numpy as np
import pandas as pd
import json
import time
import re
import os
import konlpy.tag
from ckonlpy.tag import Twitter as cTwitter
import wordcloud
import matplotlib.pyplot as plt
%matplotlib inline
import codecs
from gensim.models import word2vec
from collections import Counter
import matplotlib
from matplotlib import font_manager, rc
import platform

In [2]:
except_words = [
    r'\D+}\s\s',
    r'\[\D+\]',
    r'Copyrights\D+',
    r'<사진>',
    r'사진\=',
    r'캡처',
    r'조선일보',
    r'동아일보',
    r'한겨레',
    r'경향신문',
    r'[가-힣]{3}·[가-힣]{3} 기자 \w+@kyunghyang.com',
    r'[가-힣]{3} 기자 \w+@kyunghyang.com',
    r'www.khan.co.kr',
    r'[가-힣]{3}·[가-힣]{3} 기자 \w+@khan.kr',
    r'[가-힣]{3} 기자 \w+@khan.kr',
    r'.[가-힣]{2}\/\w{3} 기자 \w+@hani.co.kr',
    r'[가-힣]{3} [가-힣]{3} [가-힣]{3} 기자 \w+@hani.co.kr',
    r'[가-힣]{3} 기자 \w+@hani.co.kr',
    r'.[가-힣]{3} 동아닷컴 기자 \D+',
    r'.[가-힣]{3} \w+@donga.com\D+',
    r'.(\s)\w+@donga.com\D+', 
    r'\w+@donga.com\D+', 
    r'\w+@kyunghyang.com',
    r'\w+@khan.kr',
    r'\w+@hani.co.kr',
    r'[가-힣]{3}·[가-힣]{3} 기자'
    r'[가-힣]{3} 기자',
    r'플랫팀',
    r'twitter.com/\w+',
    r'바로가기',
    r'구독 신청하기',
    r'구독하기',
    r'구독신청하기',
    r'무단전재',
    r'재배포'
]

other_words1 = [
]

In [5]:
import os
# news_list = [file for file in os.listdir('.') if 'csv' in file]
news_list = r'C:\DevRoot\MyStudy\StockHelper\dataset\기사크롤링\네이버_기사_크롤링_2020.01.01_2021.12.06.csv'

In [6]:
news_list

'C:\\DevRoot\\MyStudy\\StockHelper\\dataset\\기사크롤링\\네이버_기사_크롤링_2020.01.01_2021.12.06.csv'

In [7]:
# 텍스트 데이터 정제
def data_refine(data):
    
    # 제거 패턴 (금칙어)
    for ex_word in except_words:
        data = re.sub(ex_word, '', str(data))
        
    # 치환할 패턴
    for other_word in other_words1:
        data = re.sub(other_word, 'XXX', str(data))
        
    # <br/> 태그 제거
    data = data.replace('<br/>', '')
        
    # 특수문자 제거 (알파벳, 숫자, 한글만 남기기) 
    data = re.sub(r"[^a-zA-Z0-9가-힣.]", " ", str(data))
    
    return data.strip()

In [11]:
def refine_articles(news):
    df = pd.read_csv(news).iloc[:,1:]
    df['title'] = pd.Series(map(lambda data : data_refine(data), df['title']))
    df['refine_content'] = pd.Series(map(lambda data : data_refine(data), df['content']))
    df.set_index('date', inplace=True)
    news_path = os.path.join('../정제데이터/기사', news)
    df.to_csv(news_path)

In [13]:
print(news_list)
refine_articles(news_list)

C:\DevRoot\MyStudy\StockHelper\dataset\기사크롤링\네이버_기사_크롤링_2020.01.01_2021.12.06.csv


KeyError: "None of ['date'] are in the columns"

In [12]:
refine_articles('NAVER_기사_크롤링_2020.01.01_2021.12.06.csv')
pd.read_csv('NAVER_기사_크롤링_2020.01.01_2021.12.06.csv')

Unnamed: 0                                              title  \
0             0                코스피 사상 최고치로 2020년 마감…삼성전자 ‘8만전자’ 진입   
1             1                         수원에 '반려동물 입양센터' 문 열어 [경기도]   
2             2                           제네시스 ‘GV70’ 4900만~7500만원   
3             3                                   e-경향신문 새롭게 선보입니다   
4             4         Idols Clad in IT Are Born Again as Avatars   
..          ...                                                ...   
561         561                 Korea Vaccinates 15% of Population   
562         562       High School Seniors to Be Vaccinated in July   
563         563                         Spending Disparity Deepens   
564         564  Big Businesses Cut 6,300 Jobs in Coronavirus P...   
565         565                   Tech Firms Make up Bulk of KOSPI   

           date                                            content  
0    2020.12.30   올 한해를 뜨겁게 달려온 코스피가 사상 최고가로 2020년을 마무리했다.30일 유...  
1    2020.12.15   경기도는 유기동물 입양 문화 확산을 위해 수원시 팔달구 인계동에 ‘반려동물 입양센...  
2    2020.12.08   제네시스가 중형 스포츠유틸리티차량(SUV) ‘GV70’를 8일 공개했다. 제네시스...  
3    2020.12.01  디지털 지면보기 서비스 업그레이드 경향신문 디지털 지면보기 서비스인 ‘경향뉴스진’이...  
4    2020.11.13   the avatars of the idol band, Blackpink. Cour...  
..          ...                                                ...  
561  2021.06.07  Only some 7.6 million Koreans or about 15 perc...  
562  2021.05.28  High school seniors and teachers will get thei...  
563  2021.05.24  The coronavirus pandemic has widened the dispa...  
564  2021.03.26  Big conglomerates cut 6,300 jobs amid the coro...  
565  2021.01.13  Tech companies now account for 63.3 percent of...  

[566 rows x 4 columns]

In [31]:
for news in news_list :
    print(news)
    refine_articles(news)

CJ제일제당_기사_크롤링_2020.01.01_2021.12.06.csv
DB손해보험_기사_크롤링_2020.01.01_2021.12.06.csv
GS_기사_크롤링_2020.01.01_2021.12.06.csv
GS건설_기사_크롤링_2020.01.01_2021.12.06.csv
GS리테일_기사_크롤링_2020.01.01_2021.12.06.csv
HMM_기사_크롤링_2020.01.01_2021.12.06.csv
KB금융_기사_크롤링_2020.01.01_2021.12.06.csv
KT&G_기사_크롤링_2020.01.01_2021.12.06.csv
KT_기사_크롤링_2020.01.01_2021.12.06.csv
LG_기사_크롤링_2020.01.01_2021.12.06.csv
LG디스플레이_기사_크롤링_2020.01.01_2021.12.06.csv
LG생활건강_기사_크롤링_2020.01.01_2021.12.06.csv
LG유플러스_기사_크롤링_2020.01.01_2021.12.06.csv
LG이노텍_기사_크롤링_2020.01.01_2021.12.06.csv
LG전자_기사_크롤링_2020.01.01_2021.12.06.csv
LG화학_기사_크롤링_2020.01.01_2021.12.06.csv
NAVER_기사_크롤링_2020.01.01_2021.12.06.csv
NH투자증권_기사_크롤링_2020.01.01_2021.12.06.csv
S-Oil_기사_크롤링_2020.01.01_2021.12.06.csv
SKC_기사_크롤링_2020.01.01_2021.12.06.csv
SK_기사_크롤링_2020.01.01_2021.12.06.csv
SK이노베이션_기사_크롤링_2020.01.01_2021.12.06.csv
SK텔레콤_기사_크롤링_2020.01.01_2021.12.06.csv
SK하이닉스_기사_크롤링_2020.01.01_2021.12.06.csv
강원랜드_기사_크롤링_2020.01.01_2021.12.06.csv
고려아연_기사_크롤링_2020.01.01_2021.12.06.csv

In [9]:
df_one = pd.read_csv(r'C:\DevRoot\dataset\project\삼성증권_기사_크롤링_테스트_2020.01.01_2020.12.31.csv').iloc[:,1:]
df_one['title'] = pd.Series(map(lambda data : data_refine(data), df_one['title']))
df_one['refine_content'] = pd.Series(map(lambda data : data_refine(data), df_one['content']))

In [10]:
df_one.set_index('date', inplace=True)
df_one.head()

title  \
date                                                     
2020.11.26               삼성증권 재테크 초보자들을 위한 상담  시작을 시작해   
2020.11.19           삼성증권 업계 첫  3분DC 서비스  도입 기념 이벤트 진행   
2020.10.22          삼성증권  고독한 투자가  유튜브 보면서 배우는 채권 해외주식   
2020.10.23  삼성증권  계열사 임원들에 100억 대출 의혹 금감원장  삼성증권 빨리 검사   
2020.12.01                     삼성  연말 이웃사랑 성금 500억원 기탁   

                                                      content  \
date                                                            
2020.11.26   삼성증권(사장 장석훈)은 대표 애널리스트와 삼성증권 캠페인 모델로 출연한 배우 손...   
2020.11.19   삼성증권은 업계 최초로 퇴직연금DC형 계좌를 지점 방문 없이 모바일에서 가입할 수...   
2020.10.22   삼성증권(사장 장석훈)은 재테크 초보자를 대상으로 금융상품의 개념을 쉽게 설명하는...   
2020.10.23   박용진 더불어민주당 의원은 23일 삼성증권이 2015~2018년 계열사 임원들에게...   
2020.12.01  이재용 부회장 제안 따라 ‘NGO 제휴 달력’ 30만개도 구입 삼성그룹이 올해 연말...   

                                               refine_content  
date                                                           
2020.11.26  삼성증권 사장 장석훈 은 대표 애널리스트와 삼성증권 캠페인 모델로 출연한 배우 손담...  
2020.11.19  삼성증권은 업계 최초로 퇴직연금DC형 계좌를 지점 방문 없이 모바일에서 가입할 수 ...  
2020.10.22  삼성증권 사장 장석훈 은 재테크 초보자를 대상으로 금융상품의 개념을 쉽게 설명하는 ...  
2020.10.23  박용진 더불어민주당 의원은 23일 삼성증권이 2015 2018년 계열사 임원들에게 ...  
2020.12.01  이재용 부회장 제안 따라  NGO 제휴 달력  30만개도 구입 삼성그룹이 올해 연말...

In [14]:
df_one.loc['2020.11.26', 'refine_content']

'삼성증권 사장 장석훈 은 대표 애널리스트와 삼성증권 캠페인 모델로 출연한 배우 손담비씨와 김영철씨 등이 출연해 금융 컨설팅을 진행하는  고수의 차담 을 시리즈물로 제작해 공개했다.지난 10월21일 삼성증권 공식 유튜브 채널 Samsung POP에서 공개한 이 영상은 2주 만에 총 30만뷰를 돌파했다.고수의 차담에는 삼성증권의 전 국민 재테크 캠페인인  시작을 시작해 에 출연한 배우 손담비씨와 김영철씨가 나와 재테크에 대한 전반적인 고민을 삼성증권의 애널리스트와 일대일로 상담하는 콘셉트의 영상으로 투자자들이 관심있어 할 만한 내용을 Q A 형식으로 묶어 구성했다. 고수의 차담 1편에서는 삼성증권 유튜브 채널에서 해외주식 투자 정보를 전달하는 미스터 해외주식을 진행하는 삼성증권의 장효선 수석연구위원과 배우 손담비씨가 출연했다.2편에서는 삼성증권 유튜브 채널에서  글로벌 ETF 나우 를 진행하고 있는 김도현 수석 연구위원이 배우 김영철씨와 등장해  노후 대비를 위한 투자 상품에 대해 고민하는 영상으로 진행됐다. 고수의 차담에 출연한 장효선 수석연구위원과 김도현 연구위원이 진행하는 미스터 해외주식  글로벌 ETF 나우 등은 매주 목요일 오후 4시  삼성증권 공식 유튜브 채널에서 라이브로 실시간으로 진행된다. 생방송 이후  전체 영상이 업로드돼 언제든 확인할 수 있다.  인터랙티브 자낳세에 묻다            및  금지'

In [15]:
df_two = pd.read_csv(r'C:\DevRoot\dataset\project\삼성증권_기사_크롤링_테스트_2021.01.01_2021.11.30.csv').iloc[:,1:]
df_two['title'] = pd.Series(map(lambda data : data_refine(data), df_two['title']))
df_two['refine_content'] = pd.Series(map(lambda data : data_refine(data), df_two['content']))

In [16]:
df_two.set_index('date', inplace=True)
df_two

title  \
date                                                            
2021.10.27                          삼성증권 카카오페이 청약자 44 가  MZ세대   
2021.09.26                 법원  배당 오류 낸 삼성증권  주가하락 손해액 절반 배상하라   
2021.10.21  박용진  삼성바이오에피스 임원들  2017년 삼성증권 불법 신용공여로 삼성바이오로직...   
2021.11.30                                   오미크론 변이  증시도 얼렸다   
2021.11.29                 오미크론 증시 충격 어디까지 ...기존 백신 효능 여부가 관건   
...                                                       ...   
2021.07.06                          17조 판 외국인  고배당 와 LG화학은 샀다   
2021.07.05                      30여년 만에 카카오가 불붙인 국민   이번엔 다를까   
2021.07.11                           30  치솟은 동전주... 근데 왜 불안하지   
2021.07.04           상반기 수익률 서학개미가 꼴찌  외국인 1위  기관 2위  동학개미 3위   
2021.06.25                    두 자릿수 수익률 주는 좋은 주식 찾는 노하우 TOP 3   

                                                      content  \
date                                                            
2021.10.27   삼성증권은 자사를 통해 카카오페이 공모에 참여한 청약자들의 44%가 20∼30대로...   
2021.09.26   삼성증권이 배당오류 사태로 손해를 본 투자자들에게 손해액의 절반을 배상하라는 법원...   
2021.10.21   국회 정무위원회 국정감사에서 2017년 삼성 계열사 임직원들이 삼성증권으로부터 1...   
2021.11.30   코스피 2839로 마감, 연중 최저지표 악화에 ‘공급망 병목’ 겹쳐코스피가 30일...   
2021.11.29   돌발 악재 ‘오미크론’이 던진 충격파에 글로벌 증시가 출렁이고 있다. 전문가들은 ...   
...                                                       ...   
2021.07.06  상반기 외국인 어떤 종목 샀나\t\t\t\t\t\t\t올해 국내 증시에서 외국인 투...   
2021.07.05  “포철이나 한전처럼 국민주를 만들려는 거겠죠.”(자산운용사 대표 A씨)카카오페이가 ...   
2021.07.11  주가가 1000원에도 못 미쳐 ‘동전주'로 불리는 주식들이 올 들어 30% 가까운 ...   
2021.07.04  순매수 상위 10개 종목 추정 수익률 계산해봤더니…\t\t\t\t\t\t\t“삼성전...   
2021.06.25  [방현철 박사의 머니머니] 이남우 전 메릴린치 한국 공동대표 “빅테크 중 톱픽은 아...   

                                               refine_content  
date                                                           
2021.10.27  삼성증권은 자사를 통해 카카오페이 공모에 참여한 청약자들의 44 가 20 30대로 ...  
2021.09.26  삼성증권이 배당오류 사태로 손해를 본 투자자들에게 손해액의 절반을 배상하라는 법원 ...  
2021.10.21  국회 정무위원회 국정감사에서 2017년 삼성 계열사 임직원들이 삼성증권으로부터 15...  
2021.11.30  코스피 2839로 마감  연중 최저지표 악화에  공급망 병목  겹쳐코스피가 30일 ...  
2021.11.29  돌발 악재  오미크론 이 던진 충격파에 글로벌 증시가 출렁이고 있다. 전문가들은 2...  
...                                                       ...  
2021.07.06  상반기 외국인 어떤 종목 샀나       올해 국내 증시에서 외국인 투자자들의 선택...  
2021.07.05  포철이나 한전처럼 국민주를 만들려는 거겠죠.  자산운용사 대표 A씨 카카오페이가 국...  
2021.07.11  주가가 1000원에도 못 미쳐  동전주 로 불리는 주식들이 올 들어 30  가까운 ...  
2021.07.04  순매수 상위 10개 종목 추정 수익률 계산해봤더니         삼성전자가 올해 가...  
2021.06.25  이남우 전 메릴린치 한국 공동대표  빅테크 중 톱픽은 아마존 매년 30 35  성장...  

[556 rows x 3 columns]

In [17]:
whole_news = pd.concat([df_one, df_two])
whole_news

title  \
date                                                     
2020.11.26               삼성증권 재테크 초보자들을 위한 상담  시작을 시작해   
2020.11.19           삼성증권 업계 첫  3분DC 서비스  도입 기념 이벤트 진행   
2020.10.22          삼성증권  고독한 투자가  유튜브 보면서 배우는 채권 해외주식   
2020.10.23  삼성증권  계열사 임원들에 100억 대출 의혹 금감원장  삼성증권 빨리 검사   
2020.12.01                     삼성  연말 이웃사랑 성금 500억원 기탁   
...                                                ...   
2021.07.06                   17조 판 외국인  고배당 와 LG화학은 샀다   
2021.07.05               30여년 만에 카카오가 불붙인 국민   이번엔 다를까   
2021.07.11                    30  치솟은 동전주... 근데 왜 불안하지   
2021.07.04    상반기 수익률 서학개미가 꼴찌  외국인 1위  기관 2위  동학개미 3위   
2021.06.25             두 자릿수 수익률 주는 좋은 주식 찾는 노하우 TOP 3   

                                                      content  \
date                                                            
2020.11.26   삼성증권(사장 장석훈)은 대표 애널리스트와 삼성증권 캠페인 모델로 출연한 배우 손...   
2020.11.19   삼성증권은 업계 최초로 퇴직연금DC형 계좌를 지점 방문 없이 모바일에서 가입할 수...   
2020.10.22   삼성증권(사장 장석훈)은 재테크 초보자를 대상으로 금융상품의 개념을 쉽게 설명하는...   
2020.10.23   박용진 더불어민주당 의원은 23일 삼성증권이 2015~2018년 계열사 임원들에게...   
2020.12.01  이재용 부회장 제안 따라 ‘NGO 제휴 달력’ 30만개도 구입 삼성그룹이 올해 연말...   
...                                                       ...   
2021.07.06  상반기 외국인 어떤 종목 샀나\t\t\t\t\t\t\t올해 국내 증시에서 외국인 투...   
2021.07.05  “포철이나 한전처럼 국민주를 만들려는 거겠죠.”(자산운용사 대표 A씨)카카오페이가 ...   
2021.07.11  주가가 1000원에도 못 미쳐 ‘동전주'로 불리는 주식들이 올 들어 30% 가까운 ...   
2021.07.04  순매수 상위 10개 종목 추정 수익률 계산해봤더니…\t\t\t\t\t\t\t“삼성전...   
2021.06.25  [방현철 박사의 머니머니] 이남우 전 메릴린치 한국 공동대표 “빅테크 중 톱픽은 아...   

                                               refine_content  
date                                                           
2020.11.26  삼성증권 사장 장석훈 은 대표 애널리스트와 삼성증권 캠페인 모델로 출연한 배우 손담...  
2020.11.19  삼성증권은 업계 최초로 퇴직연금DC형 계좌를 지점 방문 없이 모바일에서 가입할 수 ...  
2020.10.22  삼성증권 사장 장석훈 은 재테크 초보자를 대상으로 금융상품의 개념을 쉽게 설명하는 ...  
2020.10.23  박용진 더불어민주당 의원은 23일 삼성증권이 2015 2018년 계열사 임원들에게 ...  
2020.12.01  이재용 부회장 제안 따라  NGO 제휴 달력  30만개도 구입 삼성그룹이 올해 연말...  
...                                                       ...  
2021.07.06  상반기 외국인 어떤 종목 샀나       올해 국내 증시에서 외국인 투자자들의 선택...  
2021.07.05  포철이나 한전처럼 국민주를 만들려는 거겠죠.  자산운용사 대표 A씨 카카오페이가 국...  
2021.07.11  주가가 1000원에도 못 미쳐  동전주 로 불리는 주식들이 올 들어 30  가까운 ...  
2021.07.04  순매수 상위 10개 종목 추정 수익률 계산해봤더니         삼성전자가 올해 가...  
2021.06.25  이남우 전 메릴린치 한국 공동대표  빅테크 중 톱픽은 아마존 매년 30 35  성장...  

[1169 rows x 3 columns]

In [18]:
whole_news.to_csv(r'C:\DeepLearning_Project\StockHelper\StockHelper\test\eunkyeong\KnuSentiLex-master\data\삼성증권_기사_크롤링.csv')

In [19]:
whole_news.iloc[:,[0, 2]]

title  \
date                                                     
2020.11.26               삼성증권 재테크 초보자들을 위한 상담  시작을 시작해   
2020.11.19           삼성증권 업계 첫  3분DC 서비스  도입 기념 이벤트 진행   
2020.10.22          삼성증권  고독한 투자가  유튜브 보면서 배우는 채권 해외주식   
2020.10.23  삼성증권  계열사 임원들에 100억 대출 의혹 금감원장  삼성증권 빨리 검사   
2020.12.01                     삼성  연말 이웃사랑 성금 500억원 기탁   
...                                                ...   
2021.07.06                   17조 판 외국인  고배당 와 LG화학은 샀다   
2021.07.05               30여년 만에 카카오가 불붙인 국민   이번엔 다를까   
2021.07.11                    30  치솟은 동전주... 근데 왜 불안하지   
2021.07.04    상반기 수익률 서학개미가 꼴찌  외국인 1위  기관 2위  동학개미 3위   
2021.06.25             두 자릿수 수익률 주는 좋은 주식 찾는 노하우 TOP 3   

                                               refine_content  
date                                                           
2020.11.26  삼성증권 사장 장석훈 은 대표 애널리스트와 삼성증권 캠페인 모델로 출연한 배우 손담...  
2020.11.19  삼성증권은 업계 최초로 퇴직연금DC형 계좌를 지점 방문 없이 모바일에서 가입할 수 ...  
2020.10.22  삼성증권 사장 장석훈 은 재테크 초보자를 대상으로 금융상품의 개념을 쉽게 설명하는 ...  
2020.10.23  박용진 더불어민주당 의원은 23일 삼성증권이 2015 2018년 계열사 임원들에게 ...  
2020.12.01  이재용 부회장 제안 따라  NGO 제휴 달력  30만개도 구입 삼성그룹이 올해 연말...  
...                                                       ...  
2021.07.06  상반기 외국인 어떤 종목 샀나       올해 국내 증시에서 외국인 투자자들의 선택...  
2021.07.05  포철이나 한전처럼 국민주를 만들려는 거겠죠.  자산운용사 대표 A씨 카카오페이가 국...  
2021.07.11  주가가 1000원에도 못 미쳐  동전주 로 불리는 주식들이 올 들어 30  가까운 ...  
2021.07.04  순매수 상위 10개 종목 추정 수익률 계산해봤더니         삼성전자가 올해 가...  
2021.06.25  이남우 전 메릴린치 한국 공동대표  빅테크 중 톱픽은 아마존 매년 30 35  성장...  

[1169 rows x 2 columns]

In [111]:
refine_whole = ""

for title  in whole_news['title']:
    refine_whole += title
for content in whole_news['refine_content']:
    refine_whole += content

refine_whole

'삼성증권 재테크 초보자들을 위한 상담  시작을 시작해삼성증권 업계 첫  3분DC 서비스  도입 기념 이벤트 진행삼성증권  고독한 투자가  유튜브 보면서 배우는 채권 해외주식삼성증권  계열사 임원들에 100억 대출 의혹 금감원장  삼성증권 빨리 검사삼성  연말 이웃사랑 성금 500억원 기탁삼성증권  티클 저금통 서비스  잔돈 모아 저축과 주식 동시에삼성증권  호주 석탄산업 투자 않겠다  현지 청소년 불매운동에  백기삼성증권 투자상담도 언택트가 뜬다 베테랑들로 전담팀 구성삼성생명 삼성화재 등 삼성 금융사들  탈석탄  선언민변 참여연대  이재용 추가 고발  삼성 합병 과정  개인정보 무단 활용삼성증권 삼성전자 아마존 알리바바 세 종목 구성  랩  등 출시중국 유망 업종 집중하는  삼성 중소형FOCUS펀드  주목초분산 투자  EMP 펀드  모바일 상품권 지급 이벤트경제개혁연대  삼성그룹 계열사 이사회 구성 투명성 강화 미온적삼성생명 전영묵 카드 김대환 자산운용 심종극  86년 삼성생명 입사동기  3명 나란히 CEO 내정증권사  소비자 보호 최고책임자 잇단 선임  투자자 신뢰 되찾기12년간 15조 투자한  화력발전  손 떼고 삼성 금융 계열사  탈석탄 친환경  선언스마트 개미 로 거듭난 개인 투자자들  코로나에도 코스피 사상 최고치 견인  키워드로 보는 2020 경제  5삼성전자 수해 지역 찾아 전자제품 무상점검 서비스 온정나눔 세탁소 사랑의 밥차도 운영빚내서 부동산  가계빚 총량 최고치    빚내서 주식  증권사 대출 최대 증가증권사 대출 증가폭 8조원     역대 최대채권 매수 고객에 상품권 증정하는  채권 3 3 3  이벤트카카오게임즈 공모주 청약 분석해보니카카오게임즈  공모 첫날부터 후끈삼성  집중호우 피해 지원 30억 대한적십자사 기탁3년간 거래없던 고객 돌아오면  혜택쌀 때 사두자  투자자들 우르르 시장가격  지표가치 뛰어넘어  위험금융지주사 사외이사 보수 6660만원으로 1위 KB금융 계열사들 최고마진콜이 뭐길래 금융위 기업어음 등 유동성 점검대기업간 임